In [ ]:
%pip install langchain
%pip install langchain-core
%pip install langchain-community
%pip install pypdf
%pip install pymupdf
%pip install sentence-transformers
%pip install faiss-cpu
%pip install chromadb
%pip install langchain-groq
%pip install python-dotenv
%pip install jq

In [16]:
###Document Structure

from langchain_core.documents import Document

In [17]:
import os

#os.makedirs("../data/text_files",exist_ok=True)

In [18]:
### Directory Loader
from langchain_community.document_loaders import DirectoryLoader
from langchain_community.document_loaders import JSONLoader
import jq

loader_kwargs = {
    # .[] is used to iterate over every item in the root array
    "jq_schema": ".[]",
    
    # Specifies the key containing the main text content
    "content_keys_path": "content", 
    
    # List of keys to pull as metadata for the resulting Document object
    "metadata_keys_path": [
        "id",
        "title",
        "source",
        "date_generated"
    ],
}
#print(os.getcwd()+"/data/json/synthetic_medical_kb.json")
loader = DirectoryLoader(
    path="data/json",
    glob="**/*.json",
    loader_cls=JSONLoader,
    loader_kwargs = {
    # .[] is used to iterate over every item in the root array
    "jq_schema": ".[]",
    
    # Specifies the key containing the main text content
    "content_key": "content",
    #recursive=True, # Set to True if you have JSON files in subdirectories
    #show_progress=True # Optional: shows a progress bar during loading
    },
    recursive=True, # Set to True if you have JSON files in subdirectories
)
print(loader)
'''
loader = JSONLoader(
    file_path='../data/json/synthetic_medical_kb.json',
    jq_schema=loader_kwargs["jq_schema"],
    text_content=False)

'''
json_documents=loader.load()
#print(f"Loaded {len(json_documents)} documents.")
'''
for doc in json_documents:
    print(doc)
    print(doc.page_content)
    print("-----")
'''
json_documents

[Document(metadata={'source': '/Users/prodyotsarkar/Documents/GenAI/Capstone_Project_GenAI/data/json/synthetic_medical_kb.json', 'seq_num': 1}, page_content="Document ID: DOC-00000. This clinical abstract details the standard of care for 'Rheumatoid Arthritis'. Patients typically present with primary symptoms including unexplained weight loss, polyuria (frequent urination). The condition is primarily managed by Proton Pump Inhibitors (daily) and Statins (e.g., Atorvastatin 20mg), often under the guidance of a Pulmonology specialist. Regular follow-up appointments (quarterly or semi-annually) are required to monitor disease progression and adjust pharmacological therapy. Differential diagnoses often include conditions presenting with similar symptoms, such as general fatigue or inflammatory markers. Patient education is crucial for successful long-term management."),
 Document(metadata={'source': '/Users/prodyotsarkar/Documents/GenAI/Capstone_Project_GenAI/data/json/synthetic_medical_kb

In [19]:
import numpy as np
from sentence_transformers import SentenceTransformer
import chromadb
from chromadb.config import Settings
import uuid
from typing import List, Dict, Any, Tuple
from sklearn.metrics.pairwise import cosine_similarity



In [20]:
### Text splitting get into chunks
from langchain.text_splitter import RecursiveCharacterTextSplitter

def split_documents(documents,chunk_size=1600,chunk_overlap=300):
    """Split documents into smaller chunks for better RAG performance"""
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=chunk_size,
        chunk_overlap=chunk_overlap,
        length_function=len,
        separators=["\n\n", "\n", " ", ""]
    )
    split_docs = text_splitter.split_documents(documents)
    print(f"Split {len(documents)} documents into {len(split_docs)} chunks")
    
    # Show example of a chunk
    '''
    if split_docs:
        print(f"\nExample chunk:")
        print(f"Content: {split_docs[0].page_content[:200]}...")
        print(f"Content: {split_docs}")
        #print(f"Metadata: {split_docs[0].metadata}")
    '''
    
    for docs in split_docs:
        print(docs.page_content)
        #print(docs.metadata)
        print("-----")

    return split_docs

In [21]:
chunks=split_documents(json_documents)


Split 10500 documents into 10500 chunks
Document ID: DOC-00000. This clinical abstract details the standard of care for 'Rheumatoid Arthritis'. Patients typically present with primary symptoms including unexplained weight loss, polyuria (frequent urination). The condition is primarily managed by Proton Pump Inhibitors (daily) and Statins (e.g., Atorvastatin 20mg), often under the guidance of a Pulmonology specialist. Regular follow-up appointments (quarterly or semi-annually) are required to monitor disease progression and adjust pharmacological therapy. Differential diagnoses often include conditions presenting with similar symptoms, such as general fatigue or inflammatory markers. Patient education is crucial for successful long-term management.
-----
Document ID: DOC-00001. This clinical abstract details the standard of care for 'Coronary Artery Disease (CAD)'. Patients typically present with primary symptoms including abdominal cramping, chest pain, fatigue, joint stiffness. The co

In [ ]:
'''
from langchain.embeddings.base import Embeddings
import json
import requests
class OllamaEmbeddings(Embeddings):
    def __init__(self, model: str = "llama3.2", base_url: str = "http://localhost:11434/api/embeddings"):
        self.model = model
        self.base_url = base_url

    def embed(self,text):
        headers = {"Content-Type": "application/json"}
        payload = {
            "model": self.model,
            "prompt": text,
            "embedding": True
        }
        response = requests.post(self.base_url,headers=headers,data=json.dumps(payload))
        if response.status_code == 200:
            response_json = response.json()
            if "embedding" in response_json:
                return response_json["embedding"]
            else:
                raise ValueError("Response JSON does not contain 'embedding' key")
                return None
            
    
    def embed_documents(self, texts: List[str]) -> List[List[float]]:
        embeddings = []
        for text in texts:
            embedding = self.embed(text)
            embeddings.append(embedding)
        return embeddings

    def embed_query(self, text: str) -> List[float]:
        return self.embed_documents([text])[0]
    
ollama_embeddings = OllamaEmbeddings()
ollama_embeddings
# Test the embedding model
'''

In [22]:
class EmbeddingManager:
    def __init__(self, model_name: str = "all-MiniLM-L6-v2"): 
    #def __init__(self, model_name: str = "meta-llama/Llama-3.2-1B"):
        self.model_name = model_name
        self.model = None
        self._load_model()
    
    def _load_model(self):
        try:
            print(f"Loading model: {self.model_name}")
            self.model = SentenceTransformer(self.model_name)
            print("Model loaded successfully. Embedding dimension:", self.model.get_sentence_embedding_dimension())
        except Exception as e:
            print(f"Error loading model: {e}")
            raise


    def generate_embeddings(self, texts: List[str]) -> np.ndarray:

        if not self.model:
            raise ValueError("Model is not loaded.")
        
        print(f"Generating Embedding for {len(texts)} texts...")
        embeddings = self.model.encode(texts, show_progress_bar=True)
        print("Embeddings generated with shape:", embeddings.shape)
        return embeddings
    

embedding_manager=EmbeddingManager()
embedding_manager

Loading model: all-MiniLM-L6-v2
Model loaded successfully. Embedding dimension: 384


In [23]:
class VectorStore:
    """Manages document embeddings in a ChromaDB vector store"""
    
    def __init__(self, collection_name: str = "json_documents", persist_directory: str = "data/capstone_project/vector_store"):
        """
        Initialize the vector store
        
        Args:
            collection_name: Name of the ChromaDB collection
            persist_directory: Directory to persist the vector store
        """
        self.collection_name = collection_name
        self.persist_directory = persist_directory
        self.client = None
        self.collection = None
        self._initialize_store()

    def _initialize_store(self):
        """Initialize ChromaDB client and collection"""
        try:
            # Create persistent ChromaDB client
            os.makedirs(self.persist_directory, exist_ok=True)
            self.client = chromadb.PersistentClient(path=self.persist_directory)
            
            # Get or create collection
            self.collection = self.client.get_or_create_collection(
                name=self.collection_name,
                metadata={"description": "PDF document embeddings for RAG"}
            )
            print(f"Vector store initialized. Collection: {self.collection_name}")
            print(f"Existing documents in collection: {self.collection.count()}")
            
        except Exception as e:
            print(f"Error initializing vector store: {e}")
            raise

    def add_documents(self, documents: List[Any], embeddings: np.ndarray):
        """
        Add documents and their embeddings to the vector store
        
        Args:
            documents: List of LangChain documents
            embeddings: Corresponding embeddings for the documents
        """
        if len(documents) != len(embeddings):
            raise ValueError("Number of documents must match number of embeddings")
        
        print(f"Adding {len(documents)} documents to vector store...")
        
        # Prepare data for ChromaDB
        ids = []
        metadatas = []
        documents_text = []
        embeddings_list = []
        
        for i, (doc, embedding) in enumerate(zip(documents, embeddings)):
            # Generate unique ID
            doc_id = f"doc_{uuid.uuid4().hex[:8]}_{i}"
            ids.append(doc_id)
            
            # Prepare metadata
            metadata = dict(doc.metadata)
            metadata['doc_index'] = i
            metadata['content_length'] = len(doc.page_content)
            metadatas.append(metadata)
            
            # Document content
            documents_text.append(doc.page_content)
            
            # Embedding
            embeddings_list.append(embedding.tolist())
        
        # print(metadata)
        # Add to collection
        try:
            self.collection.add(
                ids=ids,
                embeddings=embeddings_list,
                metadatas=metadatas,
                documents=documents_text
            )
            print(f"Successfully added {len(documents)} documents to vector store")
            print(f"Total documents in collection: {self.collection.count()}")
            
        except Exception as e:
            print(f"Error adding documents to vector store: {e}")
            raise

vectorstore=VectorStore()
vectorstore

Vector store initialized. Collection: json_documents
Existing documents in collection: 21000


In [ ]:
'''
texts = [doc.page_content for doc in chunks]
print(len(texts))
for i in range(0, len(texts), 5000):
    print(f"Processing batch {i//5000 + 1}...")
    batch_texts = texts[i:i+5000]
    embeddings = ollama_embeddings.embed_documents(batch_texts)
    vectorstore.add_documents(chunks[i:i+5000], embeddings)
'''

In [24]:
texts = [doc.page_content for doc in chunks]
print(len(texts))
for i in range(0, len(texts), 5000):
    batch_texts = texts[i:i+5000]
    embeddings = embedding_manager.generate_embeddings(batch_texts)
    vectorstore.add_documents(chunks[i:i+5000], embeddings)
#embeddings = embedding_manager.generate_embeddings(texts)
#vectorstore.add_documents(chunks, embeddings)

10500
Generating Embedding for 5000 texts...


Batches: 100%|██████████| 157/157 [00:13<00:00, 11.78it/s]


Embeddings generated with shape: (5000, 384)
Adding 5000 documents to vector store...
Successfully added 5000 documents to vector store
Total documents in collection: 26000
Generating Embedding for 5000 texts...


Batches: 100%|██████████| 157/157 [00:13<00:00, 11.53it/s]


Embeddings generated with shape: (5000, 384)
Adding 5000 documents to vector store...
Successfully added 5000 documents to vector store
Total documents in collection: 31000
Generating Embedding for 500 texts...


Batches: 100%|██████████| 16/16 [00:01<00:00, 12.28it/s]


Embeddings generated with shape: (500, 384)
Adding 500 documents to vector store...
Successfully added 500 documents to vector store
Total documents in collection: 31500


In [25]:
class RAGRetriever:
    """Handles query-based retrieval from the vector store"""
    
    def __init__(self, vector_store: VectorStore, embedding_manager: EmbeddingManager):
        """
        Initialize the retriever
        
        Args:
            vector_store: Vector store containing document embeddings
            embedding_manager: Manager for generating query embeddings
        """
        self.vector_store = vector_store
        self.embedding_manager = embedding_manager

    def retrieve(self, query: str, top_k: int = 5, score_threshold: float = 0.0) -> List[Dict[str, Any]]:
        """
        Retrieve relevant documents for a query
        
        Args:
            query: The search query
            top_k: Number of top results to return
            score_threshold: Minimum similarity score threshold
            
        Returns:
            List of dictionaries containing retrieved documents and metadata
        """
        print(f"Retrieving documents for query: '{query}'")
        print(f"Top K: {top_k}, Score threshold: {score_threshold}")
        
        # Generate query embedding
        query_embedding = self.embedding_manager.generate_embeddings([query])[0]
        
        # Search in vector store
        try:
            results = self.vector_store.collection.query(
                query_embeddings=[query_embedding.tolist()],
                n_results=top_k
            )
            
            # Process results
            retrieved_docs = []
            
            if results['documents'] and results['documents'][0]:
                documents = results['documents'][0]
                metadatas = results['metadatas'][0]
                distances = results['distances'][0]
                ids = results['ids'][0]
                
                for i, (doc_id, document, metadata, distance) in enumerate(zip(ids, documents, metadatas, distances)):
                    # Convert distance to similarity score (ChromaDB uses cosine distance)
                    similarity_score = 1 - distance
                    
                    if similarity_score >= score_threshold:
                        retrieved_docs.append({
                            'id': doc_id,
                            'content': document,
                            'metadata': metadata,
                            'similarity_score': similarity_score,
                            'distance': distance,
                            'rank': i + 1
                        })
                
                print(f"Retrieved {len(retrieved_docs)} documents (after filtering)")
            else:
                print("No documents found")
            
            return retrieved_docs
            
        except Exception as e:
            print(f"Error during retrieval: {e}")
            return []

rag_retriever=RAGRetriever(vectorstore,embedding_manager)
rag_retriever

In [26]:
rag_retriever.retrieve("Tell me something abount Rheumatoid Arthritis",top_k=3,score_threshold=0.1)

Retrieving documents for query: 'Tell me something abount Rheumatoid Arthritis'
Top K: 3, Score threshold: 0.1
Generating Embedding for 1 texts...


Batches: 100%|██████████| 1/1 [00:00<00:00, 21.79it/s]

Embeddings generated with shape: (1, 384)
Retrieved 3 documents (after filtering)


[{'id': 'doc_d143b91a_1870',
  'content': "Document ID: DOC-01870. This clinical abstract details the standard of care for 'Rheumatoid Arthritis'. Patients typically present with primary symptoms including shortness of breath, polydipsia (increased thirst), joint stiffness. The condition is primarily managed by Physical therapy and Dietary modifications, often under the guidance of a Cardiology specialist. Regular follow-up appointments (quarterly or semi-annually) are required to monitor disease progression and adjust pharmacological therapy. Differential diagnoses often include conditions presenting with similar symptoms, such as general fatigue or inflammatory markers. Patient education is crucial for successful long-term management.",
  'metadata': {'source': '/Users/prodyotsarkar/Documents/GenAI/Capstone_Project_GenAI/data/json/synthetic_medical_kb.json',
   'content_length': 703,
   'seq_num': 1871,
   'doc_index': 1870},
  'similarity_score': 0.4231787919998169,
  'distance': 0.

In [27]:

### Simple RAG pipeline with Groq LLM
from langchain_groq import ChatGroq
from langchain_community.llms import ollama
import os
from dotenv import load_dotenv
load_dotenv()

### Initialize the ollama LLM
llm=ollama.Ollama(model="llama3.2",temperature=0.1)

## 2. Simple RAG function: retrieve context + generate response
def rag_simple(query,retriever,llm,top_k=3):
    ## retriever the context
    results=retriever.retrieve(query,top_k=top_k)
    '''
    for r in results:
        print(r)
        print('----')
        print(r['metadata'])
        print('-----')
        print(r['content'])
    '''
    context="\n\n".join([doc['content'] for doc in results]) if results else ""
    print("Context Retrieved:\n",context)
    print("-----")
    if not context:
        return "No relevant context found to answer the question."
    
    ## generate the answwer using GROQ LLM
    prompt=f"""Use the following context to answer the question concisely.
        Context:
        {context}

        Question: {query}

        Answer:"""
    
    print("Prompt to LLM:\n",prompt)
    response=llm.invoke([prompt.format(context=context,query=query)])
    return response

#answer=rag_simple("Can you summarize 'The River bank' chapter of the book 'The Wind in the willow' in 10 sentences?",rag_retriever,llm)
answer=rag_simple("what is indigestion and what are the treatments available?",rag_retriever,llm)
print(answer)

Retrieving documents for query: 'what is indigestion and what are the treatments available?'
Top K: 3, Score threshold: 0.0
Generating Embedding for 1 texts...


Batches: 100%|██████████| 1/1 [00:00<00:00, 24.71it/s]

Embeddings generated with shape: (1, 384)
Retrieved 3 documents (after filtering)
Context Retrieved:
 Document ID: DOC-04008. This clinical abstract details the standard of care for 'Gastroesophageal Reflux Disease (GERD)'. Patients typically present with primary symptoms including headache, unexplained weight loss. The condition is primarily managed by Dietary modifications, often under the guidance of a Pulmonology specialist. Regular follow-up appointments (quarterly or semi-annually) are required to monitor disease progression and adjust pharmacological therapy. Differential diagnoses often include conditions presenting with similar symptoms, such as general fatigue or inflammatory markers. Patient education is crucial for successful long-term management.

Document ID: DOC-04008. This clinical abstract details the standard of care for 'Gastroesophageal Reflux Disease (GERD)'. Patients typically present with primary symptoms including headache, unexplained weight loss. The condition

Gastroesophageal Reflux Disease (GERD) is a condition where stomach acid flows back up into the esophagus, causing symptoms such as headache and unexplained weight loss. Treatments for GERD include:

1. Dietary modifications under the guidance of a Pulmonology specialist.
2. Regular follow-up appointments (quarterly or semi-annually) to monitor disease progression and adjust pharmacological therapy.

Note: The question "what is indigestion" was not explicitly addressed in the provided context, but it can be inferred that GERD symptoms may include indigestion.


In [28]:
from typing import List, Dict, Any
import time

class AdvancedRAGPipeline:
    def __init__(self, retriever, llm):
        self.retriever = retriever
        self.llm = llm
        self.history = []  # Store query history

    def query(self, question: str, top_k: int = 5, min_score: float = 0.0, stream: bool = False, summarize: bool = False) -> Dict[str, Any]:
        # Retrieve relevant documents
        results = self.retriever.retrieve(question, top_k=top_k, score_threshold=min_score)
        if not results:
            answer = "No relevant context found."
            sources = []
            context = ""
        else:
            context = "\n\n".join([doc['content'] for doc in results])
            sources = [{
                'source': doc['metadata'].get('source_file', doc['metadata'].get('source', 'unknown')),
                'page': doc['metadata'].get('page', 'unknown'),
                'score': doc['similarity_score'],
                'preview': doc['content'][:120] + '...'
            } for doc in results]
            # Streaming answer simulation
            prompt = f"""Use the following context to answer the question concisely.\nContext:\n{context}\n\nQuestion: {question}\n\nAnswer:"""
            if stream:
                print("Streaming answer:")
                for i in range(0, len(prompt), 80):
                    print(prompt[i:i+80], end='', flush=True)
                    time.sleep(0.05)
                print()
            response = self.llm.invoke([prompt.format(context=context, question=question)])
            answer = response

        # Add citations to answer
        citations = [f"[{i+1}] {src['source']} (page {src['page']})" for i, src in enumerate(sources)]
        answer_with_citations = answer + "\n\nCitations:\n" + "\n".join(citations) if citations else answer

        # Optionally summarize answer
        summary = None
        if summarize and answer:
            summary_prompt = f"Tell me something about seasonal allergy about and its treatment:\n{answer}"
            summary_resp = self.llm.invoke([summary_prompt])
            summary = summary_resp

        # Store query history
        self.history.append({
            'question': question,
            'answer': answer,
            'sources': sources,
            'summary': summary
        })

        return {
            'question': question,
            'answer': answer_with_citations,
            'sources': sources,
            'summary': summary,
            'history': self.history
        }

# Example usage:
adv_rag = AdvancedRAGPipeline(rag_retriever, llm)
result = adv_rag.query("Tell me something about seasonal allergy about and its treatment?", top_k=5, min_score=0.0, stream=True, summarize=True)
print("\nFinal Answer:", result['answer'])
print('------')
print("Summary:", result['summary'])
print('------')
print("History:", result['history'][-1])

Retrieving documents for query: 'Tell me something about seasonal allergy about and its treatment?'
Top K: 5, Score threshold: 0.0
Generating Embedding for 1 texts...


Batches: 100%|██████████| 1/1 [00:00<00:00,  3.99it/s]

Embeddings generated with shape: (1, 384)
Retrieved 5 documents (after filtering)
Streaming answer:
Use the following context to answer the question concisely.
Context:
Document ID: DOC-09473. This clinical abstract details the standard of care for 'Seasonal Allergic Rhinitis'. Patients typically present with primary symptoms including polydipsia (increased thirst), chest pain, headache. The condition is primarily ma

naged by Dietary modifications, often under the guidance of a Gastroenterology specialist. Regular follow-up appointments (quarterly or semi-annually) are required to monitor disease progression and adjust pharmacological therapy. Differential diagnoses often include conditions presenting with similar symptoms, such as general fatigue or inflammatory markers. Patient education is crucial for successful long-term management.

Document ID: DOC-09473. This clinical abstract details the standard of care for 'Seasonal Allergic Rhinitis'. Patients typically present with primary symptoms including polydipsia (increased thirst), chest pain, headache. The condition is primarily managed by Dietary modifications, often under the guidance of a Gastroenterology specialist. Regular follow-up appointments (quarterly or semi-annually) are required to monitor disease progression and adjust pharmacological therapy. Differential diagnoses often include conditions presenting with similar symptoms, such as